In [1]:
import pandas as pd
import folium
from folium import plugins
from folium.vector_layers import CircleMarker
import datetime as dt
from datetime import timedelta
import time
from geopy.geocoders import Nominatim
import numpy as np

# Combined Mapping Analysis

### Historic National

In [2]:
covid = pd.read_csv('./../Mapping_Data/historic_covid_map.csv')
natdis = pd.read_csv('./../Mapping_Data/natdis_2020_map.csv')

In [3]:
covid.head()

State   Latitude  Longitude        Date  Cases  Cases_per_pop
0  Alabama  32.539527 -86.644082  2020-01-22      0            0.0
1  Alabama  32.539527 -86.644082  2020-01-23      0            0.0
2  Alabama  32.539527 -86.644082  2020-01-24      0            0.0
3  Alabama  32.539527 -86.644082  2020-01-25      0            0.0
4  Alabama  32.539527 -86.644082  2020-01-26      0            0.0

In [4]:
states = pd.read_csv('../Mapping_Data/statelatlong.csv')
states.head()

State   Latitude   Longitude        City
0    AL  32.601011  -86.680736     Alabama
1    AK  61.302501 -158.775020      Alaska
2    AZ  34.168219 -111.930907     Arizona
3    AR  34.751928  -92.131378    Arkansas
4    CA  37.271875 -119.270415  California

In [5]:
states = states[states['City'] != 'District of Columbia']
len(set(states['City']))

50

In [6]:
states.drop(columns = ['Latitude', 'Longitude'], inplace = True)
states.rename(columns = {'State' : 'state'}, inplace = True)
states.head(2)

state     City
0    AL  Alabama
1    AK   Alaska

In [7]:
covid = pd.merge(covid, states, left_on = 'State', right_on = 'City')

In [8]:
covid.drop(columns = ['State', 'City'], inplace = True)

In [9]:
covid['Cases_per_million'] = round(covid['Cases_per_pop']*100, 4)

In [10]:
covid['Cases_per_million'].sort_values(ascending = False)

203943    0.9168
203942    0.9092
203941    0.9029
203940    0.8961
203939    0.8860
           ...  
214481    0.0000
214482    0.0000
214483    0.0000
214484    0.0000
0         0.0000
Name: Cases_per_million, Length: 344606, dtype: float64

In [11]:
covid['Sqrt_Cases_per_million'] = np.sqrt(covid['Cases_per_million'])

In [12]:
natdis.head()

incidentType          incidentBeginDate               address   latitude  \
0      Tornado  2020-03-03 00:01:00+00:00     Wilson County, TN  36.146666   
1      Tornado  2020-03-03 00:01:00+00:00     Putnam County, TN  36.137987   
2      Tornado  2020-03-03 00:01:00+00:00   Davidson County, TN  36.189724   
3         Fire  2020-03-07 08:00:00+00:00     Beaver County, OK  36.762112   
4        Flood  2020-01-10 00:00:00+00:00  Milwaukee County, WI  43.018032   

    longitude  
0  -86.312000  
1  -85.455378  
2  -86.785786  
3 -100.490495  
4  -87.974087

In [13]:
natdis['incidentBeginDate'] = pd.to_datetime(natdis['incidentBeginDate'])

In [14]:
natdis['incidentBeginDate'] = natdis['incidentBeginDate'].dt.date

In [15]:
natdis['incidentBeginDate'] = pd.to_datetime(natdis['incidentBeginDate'])

In [16]:
print(type(natdis))
natdis.head(2)

<class 'pandas.core.frame.DataFrame'>


incidentType incidentBeginDate            address   latitude  longitude
0      Tornado        2020-03-03  Wilson County, TN  36.146666 -86.312000
1      Tornado        2020-03-03  Putnam County, TN  36.137987 -85.455378

In [17]:
type(natdis['incidentBeginDate'])
natdis.dtypes

incidentType                 object
incidentBeginDate    datetime64[ns]
address                      object
latitude                    float64
longitude                   float64
dtype: object

In [18]:
natdis['label'] = natdis['incidentType'] + ': ' + natdis['incidentBeginDate'].astype(str)

In [19]:
natdis.head(2)

incidentType incidentBeginDate            address   latitude  longitude  \
0      Tornado        2020-03-03  Wilson County, TN  36.146666 -86.312000   
1      Tornado        2020-03-03  Putnam County, TN  36.137987 -85.455378   

                 label  
0  Tornado: 2020-03-03  
1  Tornado: 2020-03-03

In [20]:
def choropleth_historic(c_data,
                 c_weight_col,
                 n_data,
                 n_lat_col,
                 n_lon_col,
                 n_label,
                 n_window,
                 marker_radius,
                 initial_zoom,
                 date):
    
    url = 'https://raw.githubusercontent.com/python-visualization/folium/master/examples/data'
    state_geo = f'{url}/us-states.json'
    
    map_data = c_data[c_data['Date'] == date].copy()

    testmap = folium.Map(location = [50, -95], zoom_start= initial_zoom)
    
    
    folium.Choropleth(
        geo_data=state_geo,
        bins = 9,
        name='choropleth',
        data=map_data,
        columns=['state', c_weight_col],
        key_on='feature.id',
        fill_color= 'YlGn',
        fill_opacity=.7,
        line_opacity=0.2,
        legend_name='Square Root of Total Infections per Million People'
    ).add_to(testmap)
    
    
    
    marker_data = n_data[(n_data['incidentBeginDate'] >= pd.to_datetime(date)) & (n_data['incidentBeginDate'] < pd.to_datetime(date) + timedelta(days=n_window))]

    for i, row in marker_data.iterrows():
        mark = CircleMarker(
        location = (row['latitude'], row['longitude']),
        popup = row[n_label],
            radius = marker_radius,
            fill = True,
            color = 'red',
            fill_color = 'blue',
            fill_opacity = .8
        ).add_to(testmap)
        
    
    return testmap



***Jan22***

In [21]:
min(covid['Date'])

'2020-01-22'

In [22]:
choropleth_historic(c_data = covid,
                 c_weight_col = 'Sqrt_Cases_per_million',
                 n_data = natdis,
                 n_lat_col = 'latitude',
                 n_lon_col = 'longitude',
                 n_label = 'incidentType',
                 n_window = 14,
                 marker_radius = 5,
                 initial_zoom =3,
                 date = '2020-01-23')

***Feb1***

In [23]:
choropleth_historic(c_data = covid,
                 c_weight_col = 'Sqrt_Cases_per_million',
                 n_data = natdis,
                 n_lat_col = 'latitude',
                 n_lon_col = 'longitude',
                 n_label = 'incidentType',
                 n_window = 14,
                 marker_radius = 5,
                 initial_zoom =3,
                 date = '2020-02-01')

***Feb15***

In [24]:
choropleth_historic(c_data = covid,
                 c_weight_col = 'Sqrt_Cases_per_million',
                 n_data = natdis,
                 n_lat_col = 'latitude',
                 n_lon_col = 'longitude',
                 n_label = 'incidentType',
                 n_window = 14,
                 marker_radius = 5,
                 initial_zoom =3,
                 date = '2020-02-15')

***Mar1***

In [25]:
choropleth_historic(c_data = covid,
                 c_weight_col = 'Sqrt_Cases_per_million',
                 n_data = natdis,
                 n_lat_col = 'latitude',
                 n_lon_col = 'longitude',
                 n_label = 'incidentType',
                 n_window = 14,
                 marker_radius = 5,
                 initial_zoom =3,
                 date = '2020-03-01')

***Mar19***

In [26]:
choropleth_historic(c_data = covid,
                 c_weight_col = 'Sqrt_Cases_per_million',
                 n_data = natdis,
                 n_lat_col = 'latitude',
                 n_lon_col = 'longitude',
                 n_label = 'incidentType',
                 n_window = 14,
                 marker_radius = 5,
                 initial_zoom =3,
                 date = '2020-03-19')

***Apr1***

In [27]:
choropleth_historic(c_data = covid,
                 c_weight_col = 'Sqrt_Cases_per_million',
                 n_data = natdis,
                 n_lat_col = 'latitude',
                 n_lon_col = 'longitude',
                 n_label = 'incidentType',
                 n_window = 14,
                 marker_radius = 5,
                 initial_zoom =3,
                 date = '2020-04-01')

***Apr15***

In [28]:
choropleth_historic(c_data = covid,
                 c_weight_col = 'Sqrt_Cases_per_million',
                 n_data = natdis,
                 n_lat_col = 'latitude',
                 n_lon_col = 'longitude',
                 n_label = 'incidentType',
                 n_window = 14,
                 marker_radius = 5,
                 initial_zoom =3,
                 date = '2020-04-15')

***May1***

In [29]:
choropleth_historic(c_data = covid,
                 c_weight_col = 'Sqrt_Cases_per_million',
                 n_data = natdis,
                 n_lat_col = 'latitude',
                 n_lon_col = 'longitude',
                 n_label = 'incidentType',
                 n_window = 14,
                 marker_radius = 5,
                 initial_zoom =3,
                 date = '2020-05-01')

### Projected NatDis

In [30]:
natdis_project = pd.read_csv('../Natural_Disaster_Analysis/Natural_Disaster_proj_USA_511.csv')
natdis_project.head(10)

incidentType state  beginMonth  total  yearlyrate
0         Fire    CA           7     19         1.9
1         Fire    CA           8     18         1.8
2         Fire    WA           8     17         1.7
3         Fire    OR           8     12         1.2
4         Fire    WA           7     12         1.2
5         Fire    NM           6     11         1.1
6         Fire    OK           8     10         1.0
7         Fire    AZ           6     10         1.0
8         Fire    OR           7      9         0.9
9         Fire    ID           8      8         0.8

In [31]:
test = pd.to_datetime(natdis_project['beginMonth'], format = '%m')

In [32]:
natdis_project['Date'] = pd.to_datetime(natdis_project['beginMonth'], format = '%m').apply(lambda x: x + pd.DateOffset(years=120))

In [33]:
natdis_project.dtypes

incidentType            object
state                   object
beginMonth               int64
total                    int64
yearlyrate             float64
Date            datetime64[ns]
dtype: object

In [34]:
natdis_project.head(1)

incidentType state  beginMonth  total  yearlyrate       Date
0         Fire    CA           7     19         1.9 2020-07-01

In [35]:
natdis_project['state'].isnull().sum()

0

In [36]:
states = pd.read_csv('../Mapping_Data/statelatlong.csv')
states.head()

State   Latitude   Longitude        City
0    AL  32.601011  -86.680736     Alabama
1    AK  61.302501 -158.775020      Alaska
2    AZ  34.168219 -111.930907     Arizona
3    AR  34.751928  -92.131378    Arkansas
4    CA  37.271875 -119.270415  California

In [37]:
states.drop(columns = ['City'], inplace=True)
states.head()

State   Latitude   Longitude
0    AL  32.601011  -86.680736
1    AK  61.302501 -158.775020
2    AZ  34.168219 -111.930907
3    AR  34.751928  -92.131378
4    CA  37.271875 -119.270415

In [38]:
states.rename(columns = {'State' : 'state'}, inplace = True)
states.head(2)

state   Latitude   Longitude
0    AL  32.601011  -86.680736
1    AK  61.302501 -158.775020

In [39]:
natdis_project

incidentType state  beginMonth  total  yearlyrate       Date
0           Fire    CA           7     19         1.9 2020-07-01
1           Fire    CA           8     18         1.8 2020-08-01
2           Fire    WA           8     17         1.7 2020-08-01
3           Fire    OR           8     12         1.2 2020-08-01
4           Fire    WA           7     12         1.2 2020-07-01
..           ...   ...         ...    ...         ...        ...
125        Flood    LA           8      1         0.1 2020-08-01
126   Earthquake    CA           8      1         0.1 2020-08-01
127        Flood    ID           5      1         0.1 2020-05-01
128        Flood    IA           8      1         0.1 2020-08-01
129      Volcano    HI           5      1         0.1 2020-05-01

[130 rows x 6 columns]

In [40]:
states

state   Latitude   Longitude
0     AL  32.601011  -86.680736
1     AK  61.302501 -158.775020
2     AZ  34.168219 -111.930907
3     AR  34.751928  -92.131378
4     CA  37.271875 -119.270415
5     CO  38.997934 -105.550567
6     CT  41.518784  -72.757507
7     DE  39.145251  -75.418921
8     DC  38.899349  -77.014567
9     FL  27.975728  -83.833017
10    GA  32.678125  -83.222976
11    HI  20.460000 -157.505000
12    ID  45.494576 -114.142430
13    IL  39.739318  -89.504139
14    IN  39.766219  -86.441277
15    IA  41.938317  -93.389798
16    KS  38.498779  -98.320078
17    KY  37.822294  -85.768240
18    LA  30.973377  -91.429910
19    ME  45.218513  -69.014866
20    MD  38.806352  -77.268416
21    MA  42.062940  -71.718067
22    MI  44.943560  -86.415805
23    MN  46.441859  -93.365515
24    MS  32.585106  -89.877220
25    MO  38.304662  -92.437099
26    MT  46.679800 -110.044783
27    NE  41.500819  -99.680902
28    NV  38.502032 -117.023060
29    NH  44.001231  -71.579923
30    NJ  40.143006  -74.731116
31    NM  34.166232 -106.026069
32    NY  40.705626  -73.979680
33    NC  35.214563  -79.891267
34    ND  47.467882 -100.302266
35    OH  40.190362  -82.669252
36    OK  35.309765  -98.716558
37    OR  44.141905 -120.538099
38    PA  40.994593  -77.604698
39    RI  41.582728  -71.506451
40    SC  33.625050  -80.947038
41    SD  44.212699 -100.247164
42    TN  35.830521  -85.978599
43    TX  31.169336 -100.076842
44    UT  39.499761 -111.547028
45    VT  43.871755  -72.447783
46    VA  38.003386  -79.458786
47    WA  38.899349  -77.014567
48    WV  38.920171  -80.181691
49    WI  44.786297  -89.826705
50    WY  43.000325 -107.554567

In [41]:
states.at[47, 'Latitude'] = 47.751076
states.at[47, 'Longitude'] = -120.740135

In [42]:
states[states['state'] == 'WA']

state   Latitude   Longitude
47    WA  47.751076 -120.740135

In [43]:
natdis_project_latlong = pd.merge(natdis_project, states, on = 'state')
natdis_project_latlong.rename(columns = {'Date' : 'incidentBeginDate'}, inplace = True)
natdis_project_latlong.head(5)

incidentType state  beginMonth  total  yearlyrate incidentBeginDate  \
0         Fire    CA           7     19         1.9        2020-07-01   
1         Fire    CA           8     18         1.8        2020-08-01   
2         Fire    CA           6      5         0.5        2020-06-01   
3         Fire    CA           5      4         0.4        2020-05-01   
4   Earthquake    CA           7      1         0.1        2020-07-01   

    Latitude   Longitude  
0  37.271875 -119.270415  
1  37.271875 -119.270415  
2  37.271875 -119.270415  
3  37.271875 -119.270415  
4  37.271875 -119.270415

In [44]:
set(natdis_project_latlong['incidentType'])

{'Earthquake', 'Fire', 'Flood', 'Hurricane', 'Volcano'}

In [45]:
states = pd.read_csv('../Mapping_Data/statelatlong.csv')
states = states[states['City'] != 'District of Columbia']
states.drop(columns = ['Latitude', 'Longitude'], inplace = True)

In [46]:
covid_project = pd.read_csv('../Mapping_Data/COVID_proj_US_512.csv')
covid_project.head(2)

state        date  est_new_infections  est_population  \
0  Alabama  2020-05-12          988.437485         4903185   
1  Alabama  2020-05-13          939.663255         4903185   

   daily_infection_rate  severe  
0              2.015909       1  
1              1.916434       1

In [47]:
len(set(covid_project['state']))

50

In [48]:
covid_project = pd.merge(covid_project, states, left_on = 'state', right_on = 'City')
covid_project.head(5)

state        date  est_new_infections  est_population  \
0  Alabama  2020-05-12          988.437485         4903185   
1  Alabama  2020-05-13          939.663255         4903185   
2  Alabama  2020-05-14          896.716424         4903185   
3  Alabama  2020-05-15          856.118611         4903185   
4  Alabama  2020-05-16          815.716236         4903185   

   daily_infection_rate  severe State     City  
0              2.015909       1    AL  Alabama  
1              1.916434       1    AL  Alabama  
2              1.828845       1    AL  Alabama  
3              1.746046       1    AL  Alabama  
4              1.663646       1    AL  Alabama

In [49]:
covid_project.drop(columns = ['state'], inplace = True)

In [50]:
covid_project.head(2)

date  est_new_infections  est_population  daily_infection_rate  \
0  2020-05-12          988.437485         4903185              2.015909   
1  2020-05-13          939.663255         4903185              1.916434   

   severe State     City  
0       1    AL  Alabama  
1       1    AL  Alabama

In [51]:
def choropleth_projected(c_data,
                 c_weight_col,
                 n_data,
                 n_lat_col,
                 n_lon_col,
                 n_label,
                 n_window,
                 marker_radius,
                 initial_zoom,
                 incident_type,
                 date):
    
    url = 'https://raw.githubusercontent.com/python-visualization/folium/master/examples/data'
    state_geo = f'{url}/us-states.json'
    
    map_data = c_data[c_data['date'] == date].copy()

    testmap = folium.Map(location = [50, -95], zoom_start= initial_zoom)
    
    
    folium.Choropleth(
        geo_data=state_geo,
        name='choropleth',
        data=map_data,
        columns=['State', c_weight_col],
        key_on='feature.id',
        fill_color='YlGn',
        fill_opacity=.7,
        line_opacity=0.2,
        legend_name='Projected Infections per 10,000 People / population'
    ).add_to(testmap)
    
    
    
    marker_data = n_data[(n_data['incidentBeginDate'] <= pd.to_datetime(date)) & (n_data['incidentBeginDate'] > pd.to_datetime(date) - timedelta(days=n_window)) & (n_data['incidentType'] == incident_type)]

    for i, row in marker_data.iterrows():
        mark = CircleMarker(
        location = (row['Latitude'], row['Longitude']),
        popup = row[n_label],
            radius = row[marker_radius]*20,
            fill = True,
            color = 'red',
            fill_color = 'blue',
            fill_opacity = .8
        ).add_to(testmap)
        
    
    return testmap



In [52]:
def choropleth_projected_fire(c_data,
                 c_weight_col,
                 n_data,
                 n_lat_col,
                 n_lon_col,
                 n_label,
                 n_window,
                 marker_radius,
                 initial_zoom,
                 incident_type,
                 date):
    
    url = 'https://raw.githubusercontent.com/python-visualization/folium/master/examples/data'
    state_geo = f'{url}/us-states.json'
    
    map_data = c_data[c_data['date'] == date].copy()

    testmap = folium.Map(location = [50, -95], zoom_start= initial_zoom)
    
    
    folium.Choropleth(
        geo_data=state_geo,
        name='choropleth',
        data=map_data,
        columns=['State', c_weight_col],
        key_on='feature.id',
        fill_color='YlGn',
        fill_opacity=.7,
        line_opacity=0.2,
        legend_name='Projected Infections per 10,000 People / population'
    ).add_to(testmap)
    
    
    
    marker_data = n_data[(n_data['incidentBeginDate'] <= pd.to_datetime(date)) & (n_data['incidentBeginDate'] > pd.to_datetime(date) - timedelta(days=n_window)) & (n_data['incidentType'] == incident_type)]

    for i, row in marker_data.iterrows():
        mark = CircleMarker(
        location = (row['Latitude'], row['Longitude']),
        popup = row[n_label],
            radius = row[marker_radius]*10,
            fill = True,
            color = 'red',
            fill_color = 'blue',
            fill_opacity = .8
        ).add_to(testmap)
        
    
    return testmap



## Earthquake

### May

In [53]:
choropleth_projected(c_data = covid_project,
                 c_weight_col = 'daily_infection_rate',
                 n_data = natdis_project_latlong,
                 n_lat_col = 'Latitude',
                 n_lon_col = 'Longitude',
                 n_label = 'incidentType',
                 n_window = 30,
                 marker_radius = 'yearlyrate',
                 initial_zoom =3,
                 incident_type = 'Earthquake',
                 date = '2020-05-15')

### June

In [54]:
choropleth_projected(c_data = covid_project,
                 c_weight_col = 'daily_infection_rate',
                 n_data = natdis_project_latlong,
                 n_lat_col = 'Latitude',
                 n_lon_col = 'Longitude',
                 n_label = 'incidentType',
                 n_window = 30,
                 marker_radius = 'yearlyrate',
                 initial_zoom =3,
                 incident_type = 'Earthquake',
                 date = '2020-06-15')

### July

In [55]:
choropleth_projected(c_data = covid_project,
                 c_weight_col = 'daily_infection_rate',
                 n_data = natdis_project_latlong,
                 n_lat_col = 'Latitude',
                 n_lon_col = 'Longitude',
                 n_label = 'incidentType',
                 n_window = 30,
                 marker_radius = 'yearlyrate',
                 initial_zoom =3,
                 incident_type = 'Earthquake',
                 date = '2020-07-15')

### August

In [56]:
choropleth_projected(c_data = covid_project,
                 c_weight_col = 'daily_infection_rate',
                 n_data = natdis_project_latlong,
                 n_lat_col = 'Latitude',
                 n_lon_col = 'Longitude',
                 n_label = 'incidentType',
                 n_window = 30,
                 marker_radius = 'yearlyrate',
                 initial_zoom =3,
                 incident_type = 'Earthquake',
                 date = '2020-08-04')

## Volcano

### May

In [57]:
choropleth_projected(c_data = covid_project,
                 c_weight_col = 'daily_infection_rate',
                 n_data = natdis_project_latlong,
                 n_lat_col = 'Latitude',
                 n_lon_col = 'Longitude',
                 n_label = 'incidentType',
                 n_window = 30,
                 marker_radius = 'yearlyrate',
                 initial_zoom =3,
                 incident_type = 'Volcano',
                 date = '2020-05-15')

### June

In [58]:
choropleth_projected(c_data = covid_project,
                 c_weight_col = 'daily_infection_rate',
                 n_data = natdis_project_latlong,
                 n_lat_col = 'Latitude',
                 n_lon_col = 'Longitude',
                 n_label = 'incidentType',
                 n_window = 30,
                 marker_radius = 'yearlyrate',
                 initial_zoom =3,
                 incident_type = 'Volcano',
                 date = '2020-06-15')

### July

In [59]:
choropleth_projected(c_data = covid_project,
                 c_weight_col = 'daily_infection_rate',
                 n_data = natdis_project_latlong,
                 n_lat_col = 'Latitude',
                 n_lon_col = 'Longitude',
                 n_label = 'incidentType',
                 n_window = 30,
                 marker_radius = 'yearlyrate',
                 initial_zoom =3,
                 incident_type = 'Volcano',
                 date = '2020-07-15')

### August

In [60]:
choropleth_projected(c_data = covid_project,
                 c_weight_col = 'daily_infection_rate',
                 n_data = natdis_project_latlong,
                 n_lat_col = 'Latitude',
                 n_lon_col = 'Longitude',
                 n_label = 'incidentType',
                 n_window = 30,
                 marker_radius = 'yearlyrate',
                 initial_zoom =3,
                 incident_type = 'Volcano',
                 date = '2020-08-04')

## Hurricane

### May

In [61]:
choropleth_projected(c_data = covid_project,
                 c_weight_col = 'daily_infection_rate',
                 n_data = natdis_project_latlong,
                 n_lat_col = 'Latitude',
                 n_lon_col = 'Longitude',
                 n_label = 'incidentType',
                 n_window = 30,
                 marker_radius = 'yearlyrate',
                 initial_zoom =3,
                 incident_type = 'Hurricane',
                 date = '2020-05-15')

### June

In [62]:
choropleth_projected(c_data = covid_project,
                 c_weight_col = 'daily_infection_rate',
                 n_data = natdis_project_latlong,
                 n_lat_col = 'Latitude',
                 n_lon_col = 'Longitude',
                 n_label = 'incidentType',
                 n_window = 30,
                 marker_radius = 'yearlyrate',
                 initial_zoom =3,
                 incident_type = 'Hurricane',
                 date = '2020-06-15')

### July

In [63]:
choropleth_projected(c_data = covid_project,
                 c_weight_col = 'daily_infection_rate',
                 n_data = natdis_project_latlong,
                 n_lat_col = 'Latitude',
                 n_lon_col = 'Longitude',
                 n_label = 'incidentType',
                 n_window = 30,
                 marker_radius = 'yearlyrate',
                 initial_zoom =3,
                 incident_type = 'Hurricane',
                 date = '2020-07-15')

### August

In [64]:
choropleth_projected(c_data = covid_project,
                 c_weight_col = 'daily_infection_rate',
                 n_data = natdis_project_latlong,
                 n_lat_col = 'Latitude',
                 n_lon_col = 'Longitude',
                 n_label = 'incidentType',
                 n_window = 30,
                 marker_radius = 'yearlyrate',
                 initial_zoom =3,
                 incident_type = 'Hurricane',
                 date = '2020-08-04')

## Flood

### May

In [65]:
choropleth_projected(c_data = covid_project,
                 c_weight_col = 'daily_infection_rate',
                 n_data = natdis_project_latlong,
                 n_lat_col = 'Latitude',
                 n_lon_col = 'Longitude',
                 n_label = 'incidentType',
                 n_window = 30,
                 marker_radius = 'yearlyrate',
                 initial_zoom =3,
                 incident_type = 'Flood',
                 date = '2020-05-15')

### June

In [66]:
choropleth_projected(c_data = covid_project,
                 c_weight_col = 'daily_infection_rate',
                 n_data = natdis_project_latlong,
                 n_lat_col = 'Latitude',
                 n_lon_col = 'Longitude',
                 n_label = 'incidentType',
                 n_window = 30,
                 marker_radius = 'yearlyrate',
                 initial_zoom =3,
                 incident_type = 'Flood',
                 date = '2020-06-15')

### July

In [67]:
choropleth_projected(c_data = covid_project,
                 c_weight_col = 'daily_infection_rate',
                 n_data = natdis_project_latlong,
                 n_lat_col = 'Latitude',
                 n_lon_col = 'Longitude',
                 n_label = 'incidentType',
                 n_window = 30,
                 marker_radius = 'yearlyrate',
                 initial_zoom =3,
                 incident_type = 'Flood',
                 date = '2020-07-15')

### August

In [68]:
choropleth_projected(c_data = covid_project,
                 c_weight_col = 'daily_infection_rate',
                 n_data = natdis_project_latlong,
                 n_lat_col = 'Latitude',
                 n_lon_col = 'Longitude',
                 n_label = 'incidentType',
                 n_window = 30,
                 marker_radius = 'yearlyrate',
                 initial_zoom =3,
                 incident_type = 'Flood',
                 date = '2020-08-04')

## Fire

### May

In [69]:
choropleth_projected_fire(c_data = covid_project,
                 c_weight_col = 'daily_infection_rate',
                 n_data = natdis_project_latlong,
                 n_lat_col = 'Latitude',
                 n_lon_col = 'Longitude',
                 n_label = 'incidentType',
                 n_window = 30,
                 marker_radius = 'yearlyrate',
                 initial_zoom =3,
                 incident_type = 'Fire',
                 date = '2020-05-15')

### June

In [70]:
choropleth_projected_fire(c_data = covid_project,
                 c_weight_col = 'daily_infection_rate',
                 n_data = natdis_project_latlong,
                 n_lat_col = 'Latitude',
                 n_lon_col = 'Longitude',
                 n_label = 'incidentType',
                 n_window = 30,
                 marker_radius = 'yearlyrate',
                 initial_zoom =3,
                 incident_type = 'Fire',
                 date = '2020-06-15')

### July

In [71]:
choropleth_projected_fire(c_data = covid_project,
                 c_weight_col = 'daily_infection_rate',
                 n_data = natdis_project_latlong,
                 n_lat_col = 'Latitude',
                 n_lon_col = 'Longitude',
                 n_label = 'incidentType',
                 n_window = 30,
                 marker_radius = 'yearlyrate',
                 initial_zoom =3,
                 incident_type = 'Fire',
                 date = '2020-07-15')

### August

In [72]:
choropleth_projected_fire(c_data = covid_project,
                 c_weight_col = 'daily_infection_rate',
                 n_data = natdis_project_latlong,
                 n_lat_col = 'Latitude',
                 n_lon_col = 'Longitude',
                 n_label = 'incidentType',
                 n_window = 30,
                 marker_radius = 'yearlyrate',
                 initial_zoom =3,
                 incident_type = 'Fire',
                 date = '2020-08-04')

In [73]:
def choropleth_projected_covid(c_data,
                 c_weight_col,
                 initial_zoom,
                 date):
    
    url = 'https://raw.githubusercontent.com/python-visualization/folium/master/examples/data'
    state_geo = f'{url}/us-states.json'
    
    map_data = c_data[c_data['date'] == date].copy()

    testmap = folium.Map(location = [50, -95], zoom_start= initial_zoom)
    
    
    folium.Choropleth(
        geo_data=state_geo,
        name='choropleth',
        data=map_data,
        columns=['State', c_weight_col],
        key_on='feature.id',
        fill_color='Reds',
        fill_opacity=.7,
        line_opacity=0.2,
        legend_name='States with Severe Infection Rates'
    ).add_to(testmap)
    
    return testmap



In [74]:
choropleth_projected_covid(c_data = covid_project,
                 c_weight_col = 'severe',
                 initial_zoom =3,
                 date = '2020-05-15')

In [75]:
choropleth_projected_covid(c_data = covid_project,
                 c_weight_col = 'severe',
                 initial_zoom =3,
                 date = '2020-06-01')

In [76]:
def choropleth_projected_fire_nocovid(
                 n_data,
                 n_lat_col,
                 n_lon_col,
                 n_label,
                 n_window,
                 marker_radius,
                 initial_zoom,
                 incident_type,
                 date):
    
    testmap = folium.Map(location = [50, -95], zoom_start= initial_zoom)
    
    
    
    
    marker_data = n_data[(n_data['incidentBeginDate'] <= pd.to_datetime(date)) & (n_data['incidentBeginDate'] > pd.to_datetime(date) - timedelta(days=n_window)) & (n_data['incidentType'] == incident_type)]

    for i, row in marker_data.iterrows():
        mark = CircleMarker(
        location = (row['Latitude'], row['Longitude']),
        popup = row[n_label],
            radius = row[marker_radius]*10,
            fill = True,
            color = 'red',
            fill_color = 'blue',
            fill_opacity = .8
        ).add_to(testmap)
        
    
    return testmap



In [77]:
choropleth_projected_fire_nocovid(
                 n_data = natdis_project_latlong,
                 n_lat_col = 'Latitude',
                 n_lon_col = 'Longitude',
                 n_label = 'incidentType',
                 n_window = 30,
                 marker_radius = 'yearlyrate',
                 initial_zoom =3,
                 incident_type = 'Fire',
                 date = '2020-06-04')

In [78]:
choropleth_projected_fire_nocovid(
                 n_data = natdis_project_latlong,
                 n_lat_col = 'Latitude',
                 n_lon_col = 'Longitude',
                 n_label = 'incidentType',
                 n_window = 30,
                 marker_radius = 'yearlyrate',
                 initial_zoom =3,
                 incident_type = 'Fire',
                 date = '2020-08-04')